In [1]:
from matplotlib import pyplot as plt
%matplotlib notebook

In [2]:
import folium
from folium import Map, CircleMarker, Vega, Popup
from vincent import Bar

In [3]:
import pandas as pd
import numpy as np
import sqlite3
from scipy.spatial import ConvexHull

In [4]:
from src.get_historic_missions import *

In [5]:
from  rtree import index
import glob
from src.read_timeGeo import read_timeGeo
import argparse
import src.global_settings as gl
from src.db_skeleton import dbs_class
from src.tools.toECEF import toECEF
from src.tools.toGeodetic import toGeodetic
from src.tools.cg_convex_hull import cg_convex_hull
from src.tools.own_bb import own_bb_Geo
from itertools import product

In [6]:
class dummy_args:
    def __init__(self):
        self.db="temp_1.db3"
        
gl.args = dummy_args()

In [7]:
gl.args.db

'temp_1.db3'

In [8]:
rtree_idx,timeGeoList,db=get_historic_missions()

In [10]:
def bb_to_line(bb):
    return [[bb[0],bb[1]],
            [bb[0],bb[3]],
            [bb[2],bb[3]],
            [bb[2],bb[1]],
            [bb[0],bb[1]]]
def kasten(la,lo):
    cf=0.00001*5
    bb=[la-cf,lo-cf,la+cf,lo+cf]
    return bb_to_line(bb)

In [49]:

##a=[]
yy=[]
xx=[]
for idx in range(550,570,50):
    r=timeGeoList[idx]
    G0,G1,G=r.get_externals(True)
    p=np.polyfit(G[:,0],G[:,1],1)
    ryaw=np.arctan(p[0])
    yy.append(r.yaw)
    xx.append(G.mean(axis=0))
yaw=np.mean(yy)
yaw=np.pi/8*1.14
dm=np.array([[np.cos(yaw),-np.sin(yaw)],[np.sin(yaw),np.cos(yaw)]])
c=np.mean(xx,axis=0)

In [50]:
N=len(timeGeoList[0].lat)
x,y=timeGeoList[0].lat[N//2],timeGeoList[0].lon[N//2]
m=folium.Map([x,y],zoom_start=17)

for idx in range(550,570,50):
    r=timeGeoList[idx]    
    fg_ = folium.FeatureGroup(name=str(idx))
    N=len(r.lat)
    x,y=r.lat[N//2],r.lon[N//2]
    s1=s2=0.5 #1/128.0
    x0,y0,x1,y1=r.rtree_bb
    fx,fy=r.rtree_bb[2]-r.rtree_bb[0],r.rtree_bb[3]-r.rtree_bb[1]
    pp=lambda sc1,sc2:[x0+sc1*fx,y0+sc1*fy,x0+sc2*fx,y0+sc2*fy]
    pop=f"{idx,r.speed.mean(),np.rad2deg(r.yaw.mean())}"
    folium.PolyLine(bb_to_line(pp(0.5-s1,0.5+s2)),popup=pop,).add_to(m)
    #folium.PolyLine(bb_to_line(pp(0.3,0.7)),popup=str(idx)).add_to(m)
    ##cars = pd.DataFrame({'x':r.perc,'y':r.yaw*180.0/np.pi})
    ##a.append(alt.Chart(cars).mark_point().encode(x='x',y='y'))
    ##popup = folium.Popup(max_width=650)
    ##folium.VegaLite(a[-1], height=350, width=650).add_to(popup)
    folium.PolyLine(kasten(x,y),popup=pop).add_to(fg_)
    G0,G1,G=r.get_externals(True)
    
    G1=G1-c
    G1=np.matmul(dm,G1.transpose()).transpose()
    G1=G1+c
    
    G0=G0-c
    G0=np.matmul(dm,G0.transpose()).transpose()
    G0=G0+c
    
    G=G-c
    G=np.matmul(dm,G.transpose()).transpose()
    G=G+c
    
    folium.PolyLine(G0,color="green").add_to(fg_)
    folium.PolyLine(G1,color="red").add_to(fg_)
    folium.PolyLine(G,color="black").add_to(fg_)
    GG=np.concatenate((G0,G1))
    dd=ConvexHull(GG)
    folium.PolyLine(GG[dd.vertices],color="magenta").add_to(fg_)

    
    m.add_child(fg_)

folium.LayerControl(collapsed=False).add_to(m)
m